<a href="https://colab.research.google.com/github/Manuelstv/astro-ml/blob/main/ROTATION_SUBTRACTION.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#install libraries
#%matplotlib inline
!pip install -U -q astropy


In [ ]:
#!/usr/bin/python

import astropy.io.fits
from astropy.io import fits
from astropy.io.fits import *
import numpy as np
from scipy import ndimage
import string
import os
import sys
import math
import matplotlib.pyplot as plt
import matplotlib.cm as cm
from scipy import stats
import matplotlib.patches as mpatches

In [ ]:
from google.colab import drive

# authorize it

In [ ]:
drive.mount('/content/drive')


Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [ ]:
%cd "/content/drive/My Drive/NewData/SpaceBasedTraining/Data/agrupp"

/content/drive/My Drive/NewData/SpaceBasedTraining/Data/agrupp


In [ ]:

def in_circle(xc, yc, r, x, y):
	"""
	Function to check if x and y coordinates are within the circle of
	radius r centered at xc,yc.
	"""
	
	square_dist = (xc - x) ** 2 + (yc - y) ** 2

	return square_dist <= r ** 2

In [ ]:
def getPeak(img_data,x,y,sigma):
	"""
	Function developed by Tom Collett. It find the central position of 
	the galaxy by applying a Gaussian filter. 
	"""

	from scipy import ndimage
	for i in range(3):
		d = ndimage.gaussian_filter(img_data[y-20:y+20,x-20:x+20],sigma)[13:-13,13:-13]
		Y,X = np.mgrid[0:d.shape[0],0:d.shape[1]]
		Y = Y - Y.mean()
		X = X - X.mean()
		d = d/d.sum()
		x = x+int(np.round((d*X).sum()))
		y = y+int(np.round((d*Y).sum()))
	
	return x,y


In [ ]:
def getCentre(img_data,size,radius):
	"""
	Get centre of galaxy (brigthness distribution) by minimizing the residuals 
	in the rotated-subtracted image.
	Use only central region to compute centre. 
	"""

	import scipy.optimize as optimization

#	Initial guess for function minimization: using 
#	xci,yci=getPeak(resampled_data,resampled_data.shape[0]/2,resampled_data.shape[1]/2)

	xci=img_data.shape[0]/2
	yci=img_data.shape[1]/2
	
	img_data_red=img_data[yci-size:yci+size,xci-size:xci+size]

	size=float(size)
	# initial values for centre in the new origin
	xci=size
	yci=size

	c0=np.array((yci,xci))

	yc,xc=optimization.fmin(f_to_min,c0,args=(img_data_red,radius))
	
	# converting yc and xc to the original image origin
	yc=float(img_data.shape[0])/2.-size+yc
	xc=float(img_data.shape[1])/2.-size+xc


	return yc,xc




In [ ]:
def f_to_min(centre,img_data,radius):
	"""		
 	Function to be minimize in order to find the centre of the brightness 
	distribution: sum of the squares of counts in rotated-subtracted image.
	"""
	rot_sub_data=rotate_subtract(centre,img_data)

	y,x=np.mgrid[0:rot_sub_data.shape[0],0:rot_sub_data.shape[1]]

	yc=rot_sub_data.shape[0]/2.
	xc=rot_sub_data.shape[1]/2.
	
	square_dist = (x-xc) ** 2 + (y-yc) ** 2
	

	return (rot_sub_data[square_dist <= radius**2]**2).sum()


In [ ]:
def rotate_subtract(centre,img_data):
	"""	
 	Rotation subtraction method.
 	Firts shift image to have the centre of galaxy at the centre of image.
 	Then rotate 180 degrees and finally subtract rotated from the original
	image.
	"""		

	offset=np.array(img_data.shape)/2.-np.array(centre)
	shifted_data=ndimage.shift(img_data,offset,order=3,mode='constant')
	rotated_data=ndimage.rotate(shifted_data,180.,mode='constant',reshape=False)
	rot_sub_data=shifted_data-rotated_data
	
	return rot_sub_data

#Be careful with the index (id)

In [ ]:
#Definition of parameters -> put them in a configuration file
sampling_factor=3. #sampling of original image
pixel_scale=0.27	
sampling_pixscale=pixel_scale/sampling_factor

nbins=20 # number of angle bins in each ring

dr=2*sampling_factor # ring thickness; ring r=2 pix in original image
r0=5*sampling_factor # radius of the first ring
n_rings=5 # number of rings

id = 100000
#while id<120000:
while id<120000:
  
#	image_name='LensingOn_190_r_SDSS_img.fits'
  image_root=string.split('imageEUC_VIS-'+str(id)+'.fits',sep='.')[0]

# 	Read and resample image
  original_data=fits.getdata('imageEUC_VIS-'+str(id)+'.fits',ignore_missing_end=True)

	#with fits.open(image_name, ignore_missing_end=True) as hdus:
	#	original_data=hdus.info()
  resampled_data=ndimage.zoom(original_data, sampling_factor, order=3)

# 	Get centre of galaxy
  yc,xc=getCentre(resampled_data,int(15.*sampling_factor), int(3.5*sampling_factor))
  centre=np.array((yc,xc))

# 	Rotation subtraction
  rot_sub_data=rotate_subtract(centre,resampled_data)
	
	# Since the rotation-subtraction computes shifts the image to have the 
	# centre of the galaxy in the centre of the image, redefine the centre 	
	# of galaxy as centre of 	
  xc=float(rot_sub_data.shape[1])/2.
  yc=float(rot_sub_data.shape[0])/2.
		
#	Write output 
  output_file=image_root+'_rotsub.fits'
  #offset=np.array(rot_sub_data.shape)/2.-np.array(centre)
  #output_data=ndimage.shift(rot_sub_data,offset*(1.),order=3,mode='constant')
  output_data=ndimage.zoom(rot_sub_data, 1./sampling_factor, order=3)
  fits.writeto(output_file,output_data,clobber=True)
  print id
  id =id+1

# 

Optimization terminated successfully.
         Current function value: 0.000000
         Iterations: 33
         Function evaluations: 68
100000
Optimization terminated successfully.
         Current function value: 0.000000
         Iterations: 34
         Function evaluations: 68
100001
Optimization terminated successfully.
         Current function value: 0.000000
         Iterations: 31
         Function evaluations: 66
100002
Optimization terminated successfully.
         Current function value: 0.000000
         Iterations: 36
         Function evaluations: 72
100003
Optimization terminated successfully.
         Current function value: 0.000000
         Iterations: 32
         Function evaluations: 67
100004
Optimization terminated successfully.
         Current function value: 0.000000
         Iterations: 32
         Function evaluations: 64
100005
Optimization terminated successfully.
         Current function value: 0.000000
         Iterations: 35
         Function evaluati